In [1]:
from dnd.monsters.circus_fighter import create_warrior
from dnd.entity import Entity
from dnd.blocks.equipment import WeaponSlot
from dnd.core.dice import Dice, RollType, AttackOutcome
from uuid import uuid4
from dnd.core.events import EventQueue

import time
from uuid import UUID



In [2]:
start_time = time.time()
source_id = uuid4()
proficiency_bonus = 2

In [3]:
q = EventQueue()

In [4]:
warrior = create_warrior(source_id,proficiency_bonus,position=(0,0))
# q._all_events


In [5]:
warrior2 = create_warrior(name="Mona",position=(1,1))
# q._all_events
#create 100 warriors


In [6]:
from dnd.core.events import Event, EventType, EventPhase
from typing import Optional
from dnd.core.base_tiles import floor_factory

In [7]:

#floor from 0 to 100 in a100 by 100 grid
floors = [floor_factory((i,j)) for i in range(30) for j in range(30)]


In [8]:
from dnd.actions import Attack, AttackEvent, Move, MovementEvent
weapon_slot = WeaponSlot.MAIN_HAND

In [9]:
Entity.update_all_entities_senses()


In [10]:
attack = Attack(name="Warrior Main Hand attack",
                source_entity_uuid=warrior.uuid,
                target_entity_uuid=warrior2.uuid,
                weapon_slot= WeaponSlot.MAIN_HAND)
                
attack2=Attack(name="Warrior2 Main Hand attack",
               source_entity_uuid=warrior2.uuid,
               target_entity_uuid=warrior.uuid,
               weapon_slot= WeaponSlot.MAIN_HAND)


In [11]:
from dnd.reactions import create_opputinity_attack_handler

In [12]:
# opputinity_attack_handler_warrior = create_opputinity_attack_handler(warrior.uuid)

# warrior.add_event_handler(opputinity_attack_handler_warrior)


In [13]:
Entity.update_all_entities_senses()

print(warrior.senses.paths)

defaultdict(<class 'list'>, {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)], (0, 2): [(0, 0), (0, 1), (0, 2)], (1, 2): [(0, 0), (0, 1), (1, 2)], (2, 0): [(0, 0), (1, 0), (2, 0)], (2, 1): [(0, 0), (1, 0), (2, 1)], (2, 2): [(0, 0), (1, 1), (2, 2)], (0, 3): [(0, 0), (0, 1), (0, 2), (0, 3)], (1, 3): [(0, 0), (0, 1), (0, 2), (1, 3)], (3, 0): [(0, 0), (1, 0), (2, 0), (3, 0)], (3, 1): [(0, 0), (1, 0), (2, 0), (3, 1)], (2, 3): [(0, 0), (0, 1), (1, 2), (2, 3)], (3, 2): [(0, 0), (1, 0), (2, 1), (3, 2)], (3, 3): [(0, 0), (1, 1), (2, 2), (3, 3)], (0, 4): [(0, 0), (0, 1), (0, 2), (0, 3), (0, 4)], (1, 4): [(0, 0), (0, 1), (0, 2), (1, 3), (1, 4)], (4, 0): [(0, 0), (1, 0), (2, 0), (3, 0), (4, 0)], (4, 1): [(0, 0), (1, 0), (2, 0), (3, 1), (4, 1)], (2, 4): [(0, 0), (0, 1), (0, 2), (1, 3), (2, 4)], (4, 2): [(0, 0), (1, 0), (2, 0), (3, 1), (4, 2)], (3, 4): [(0, 0), (0, 1), (1, 2), (2, 3), (3, 4)], (4, 3): [(0, 0), (1, 0), (2, 1), (3, 2), (4, 3)], (4, 4): [(0

In [14]:
movement = Move(name="Warrior Movement",
                    source_entity_uuid=warrior.uuid,
                    end_position=(2,2))

movement2 = Move(name="Warrior2 Movement",
                source_entity_uuid=warrior2.uuid,
                end_position=(2,2))

In [15]:
movement2.costs

[Cost(name='Movement Cost', cost_type='movement', cost=0, evaluator=<function entity_action_economy_cost_evaluator at 0x0000020001FC56C0>)]

In [16]:
start_time = time.time()



In [17]:
start_time = time.time()

movement2.pre_validate()
print(time.time()-start_time)


0.0


In [18]:
print(warrior2.senses.paths)

defaultdict(<class 'list'>, {})


In [19]:
warrior.senses.get_threathened_positions()

[(0, 1), (1, 0), (1, 1)]

In [20]:
print(warrior.position)
start_time = time.time()
movement2.apply()
print(time.time()-start_time)
print(warrior.position)


(0, 0)
0.0019974708557128906
(0, 0)


In [21]:
start_time = time.time()

Entity.update_all_entities_senses()
print(time.time()-start_time)


0.008012533187866211


In [22]:
from dnd.core.events import Trigger, EventHandler, EventProcessor

In [23]:
attack_trigger = Trigger(name="Attack Trigger",
                         event_type=EventType.ATTACK,
                         event_phase=EventPhase.DECLARATION)



def attack_processor(event: AttackEvent, source_entity_uuid: UUID ) -> Optional[AttackEvent]:
    print(f"Simple Attack event received for {source_entity_uuid} with target {event.target_entity_uuid} in phase {event.phase}")
    return event

def precise_attack_processor(event: AttackEvent, source_entity_uuid: UUID ) -> Optional[AttackEvent]:
    print(f"Precise attack event received for {source_entity_uuid} with target {event.target_entity_uuid} in phase {event.phase}")
    return event

test_handler = EventHandler(name="Test Handler",
                            trigger_conditions=[attack_trigger],
                            event_processor=attack_processor,
                            source_entity_uuid=warrior2.uuid)



precise_attack_trigger = Trigger(name="Attack Trigger",
                         event_type=EventType.ATTACK,
                         event_phase=EventPhase.DECLARATION,
                         event_source_entity_uuid=warrior.uuid,
                         event_target_entity_uuid=warrior2.uuid)
test_precise_handler = EventHandler(name="Test Precise Handler",
                                    trigger_conditions=[precise_attack_trigger],
                                    event_processor=precise_attack_processor,
                                    source_entity_uuid=warrior2.uuid)



In [24]:
test_handler.trigger_conditions[0].is_simple()

True

In [25]:
warrior2.add_event_handler(test_handler)
warrior2.add_event_handler(test_precise_handler)

In [26]:
warrior2.get_hp()

58

In [27]:
# Trigger condition: event_type=<EventType.ATTACK: 'attack'> event_phase=<EventPhase.DECLARATION: 'declaration'> event_source_entity_uuid=UUID('7f40519e-37ae-411d-81e9-90fafbccdd92') event_target_entity_uuid=UUID('9ec24cff-1dc5-4af7-a768-db9962dea6ea')


In [28]:
#measure time of attack
start_time = time.time()
attack.apply()
attack_time = time.time()-start_time
print(f"Attack time: {attack_time}")

Simple Attack event received for ab7d3f7a-4281-426e-81da-c347d2a49231 with target ab7d3f7a-4281-426e-81da-c347d2a49231 in phase EventPhase.DECLARATION
Precise attack event received for ab7d3f7a-4281-426e-81da-c347d2a49231 with target ab7d3f7a-4281-426e-81da-c347d2a49231 in phase EventPhase.DECLARATION
Attack time: 0.0020096302032470703


In [29]:
warrior2.remove_event_handler(test_handler)

In [30]:
attack2.apply()

AttackEvent(name='Warrior2 Main Hand attack', uuid=UUID('71cba55f-49ed-48b2-bfb9-fac924477378'), source_entity_uuid=UUID('ab7d3f7a-4281-426e-81da-c347d2a49231'), source_entity_name=None, target_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), target_entity_name=None, context=None, use_register=True, lineage_uuid=UUID('b8daddce-b723-4dc9-a5ba-ec73359051d7'), timestamp=datetime.datetime(2025, 5, 18, 17, 43, 42, 749741), event_type=<EventType.ATTACK: 'attack'>, phase=<EventPhase.CANCEL: 'cancel'>, modified=True, canceled=True, parent_event=None, status_message='Target entity not in reach for Warrior2 Main Hand attack', lineage_children_events=[], children_events=[], costs=[Cost(name='Attack Cost', cost_type='actions', cost=1, evaluator=<function entity_action_economy_cost_evaluator at 0x0000020001FC56C0>)], weapon_slot=<WeaponSlot.MAIN_HAND: 'MAIN_HAND'>, range=None, attack_bonus=None, ac=None, dice_roll=None, attack_outcome=None, damages=None, damage_rolls=None)

In [31]:
warrior.get_damages(weapon_slot=WeaponSlot.MAIN_HAND,target_entity_uuid=warrior.uuid)

[Damage(name='Damage', uuid=UUID('927f73e5-2ab8-469b-a48e-67eac822cac6'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, damage_dice=6, dice_numbers=1, damage_bonus=ModifiableValue(name='Damage Bonus_strength Ability Score_strength Modifier Bonus_Melee Damage Bonus_Damage Bonus', uuid=UUID('9c16804c-b388-43cd-9d44-29f5eb227666'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), target_entity_name=None, context=None, use_register=True, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000002007FB4ECA0>, generated_from=[UUID('c98433b4-7c9e-4749-b802-fbaf62cee4e6'), UUID('5198d1f9-a67c-44f6-8a58-3f837d67ff12'), UUID('789e373c-219d-4f97-8c56-87e199ada2b3'), UUID('c98433b4-7c9e-4749-b802-fbaf62cee4e6')], global_normalizer=False, self_static

In [32]:
for event in q._all_events:
    print(event.name,event.status_message)


Performer's Leather Armor None
Performer's Leather Armor None
Performer's Leather Armor None
Performer's Leather Armor None
Flaming Scimitar None
Flaming Scimitar None
Flaming Scimitar None
Flaming Scimitar None
Rusty Dagger None
Rusty Dagger None
Rusty Dagger None
Rusty Dagger None
Dual Wielder None
Dual Wielder Applied Dual Wielder contextual ac modifer condition to Ganger
Dual Wielder Applied Dual Wielder contextual ac modifer condition to Ganger
Elemental Weapon Mastery None
Elemental Weapon Mastery Applied Elemental Weapon Mastery contextual advantage modifier condition to Ganger
Elemental Weapon Mastery Applied Elemental Weapon Mastery contextual advantage modifier condition to Ganger
Elemental Affinity None
Elemental Affinity Applied Elemental Affinity resistance modifier condition to Ganger
Elemental Affinity Applied Elemental Affinity resistance modifier condition to Ganger
Circus Performer None
Circus Performer Applied Circus Performer condition to Ganger
Circus Performer App

In [33]:
warrior2.get_hp()

58

In [34]:
warrior.action_economy.actions.normalized_score

1

In [35]:
warrior.action_economy.actions.self_static.value_modifiers

{UUID('9306b596-7b23-443f-a6a7-5da061f8003e'): NumericalModifier(name='Actions_base_value', uuid=UUID('9306b596-7b23-443f-a6a7-5da061f8003e'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), target_entity_name=None, context=None, use_register=True, value=1, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000002007FB4F6A0>, normalized_value=1)}

In [36]:
warrior.action_economy.reset_all_costs()

In [37]:
warrior.action_economy.actions.normalized_score

1

In [38]:
warrior.source_entity_uuid

UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e')

In [39]:
warrior.ability_scores.uuid


UUID('349e1bd3-d56c-4b38-8a67-8f41e3d679ea')

In [40]:
Entity.get(warrior.source_entity_uuid)

Entity(name='Ganger', description='A level 4 fighter character with a past in the circus and spiked claws for hands.', uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={UUID('349e1bd3-d56c-4b38-8a67-8f41e3d679ea'): AbilityScores(name='ability_scores', description=None, uuid=UUID('349e1bd3-d56c-4b38-8a67-8f41e3d679ea'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={UUID('3ae70825-45bb-4eeb-b61f-c1100684ddb3'): Ability(name='strength', description=None, uuid=UUID('3ae70825-45bb-4eeb-b61f-c1100684ddb3'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={}, values={UUID('ead381aa-ccdc-4a03-9c71-25a5fa91f56

In [41]:
from dnd.conditions import Paralyzed

In [42]:
paralyzed_condition = Paralyzed(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)
paralyzed_condition.apply()


ConditionApplicationEvent(name='Paralyzed', uuid=UUID('c0c31909-672e-450e-8c8c-b8d213568047'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=UUID('ab7d3f7a-4281-426e-81da-c347d2a49231'), target_entity_name=None, context=None, use_register=True, lineage_uuid=UUID('91831eb9-bb7c-4fc9-b124-71bd99dd101a'), timestamp=datetime.datetime(2025, 5, 18, 17, 43, 43, 92637), event_type=<EventType.CONDITION_APPLICATION: 'condition_application'>, phase=<EventPhase.COMPLETION: 'completion'>, modified=True, canceled=False, parent_event=None, status_message='Applied Paralyzed to target contextual critical modifier to Warrior 99', lineage_children_events=[UUID('0b54e087-5388-4b0f-b43a-389e08808dae'), UUID('0887ad38-29ad-4349-a821-1db98abbfa83'), UUID('d6340a82-2c16-41b5-93c8-36a898d23957'), UUID('aea866ba-a37d-4652-94e8-b82e9bbc3a07'), UUID('57a3f294-6c27-4e49-a196-34cfc5f1e4b8'), UUID('505f521f-cd17-4666-8181-9ed021a87144'), UUID('0b54e087-5

In [43]:
weapon_slot = WeaponSlot.MAIN_HAND

warrior_bonus = warrior.attack_bonus(target_entity_uuid=warrior2.source_entity_uuid,weapon_slot=weapon_slot)

In [44]:
warrior.ability_scores.get_ability("strength").ability_score.normalized_score+warrior.ability_scores.get_ability("strength").modifier_bonus.normalized_score



4

In [45]:
warrior_bonus.normalized_score

5

In [46]:
attack_dice = Dice(count=1,value=20,bonus=warrior_bonus, roll_type=RollType.ATTACK)
attack_roll = attack_dice.roll
print(f"Attack roll result: {attack_roll.total}")








Attack roll result: 15


In [47]:
attack_roll.bonus

5

In [48]:
attack_roll.results

10

In [49]:
import time

In [50]:
start_time = time.time()
damages = warrior.get_damages(weapon_slot)
print(time.time()-start_time)

0.0004990100860595703


In [51]:
start_time = time.time()
attack_bonus = warrior.attack_bonus(weapon_slot= weapon_slot)
print(time.time()-start_time)


0.0004990100860595703


In [52]:
start_time = time.time()
ac = warrior2.ac_bonus()
print(time.time()-start_time)
start_time = time.time()

0.000499725341796875


In [53]:
damages

[Damage(name='Damage', uuid=UUID('97022ca8-3d61-426d-ad35-a1fb1fbb7c2e'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, damage_dice=6, dice_numbers=1, damage_bonus=ModifiableValue(name='Damage Bonus_strength Ability Score_strength Modifier Bonus_Melee Damage Bonus_Damage Bonus', uuid=UUID('8f142e3e-8a7b-4d00-bf85-165b4d3d1ea9'), source_entity_uuid=UUID('e3da80a6-11c8-41c9-8fd1-45d395b0669e'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000002007FB4ECA0>, generated_from=[UUID('c98433b4-7c9e-4749-b802-fbaf62cee4e6'), UUID('b5339d9c-2673-4bb5-821e-e86d52279387'), UUID('789e373c-219d-4f97-8c56-87e199ada2b3'), UUID('c98433b4-7c9e-4749-b802-fbaf62cee4e6')], global_normalizer=False, self_static=StaticValue(name='A Value_A Value_A Val

In [54]:
start_time = time.time()
warrior.set_target_entity(warrior2.uuid)
print(time.time()-start_time)

0.0015001296997070312


In [55]:
warrior.target_entity_uuid=warrior2.uuid

In [56]:
a = warrior.uuid

In [57]:
start_time = time.time()
warrior2.target_entity_name="warrior.uuid"
print(time.time()-start_time)

0.0


In [58]:
start_time = time.time()
warrior2.target_entity_uuid=warrior.uuid
print(time.time()-start_time)

0.0


In [59]:
start_time = time.time()
warrior2.set_target_entity(warrior.uuid)
print(time.time()-start_time)

0.0014982223510742188


In [60]:
start_time = time.time()
warrior2.set_target_entity(warrior.uuid)
print(time.time()-start_time)

0.0015106201171875


In [61]:
start_time = time.time()
warrior.attack(warrior2.uuid,weapon_slot)
print(time.time()-start_time)


AttributeError: 'Entity' object has no attribute 'attack'

In [28]:
warrior_strenght_modifer = warrior.ability_scores.get_ability("strength").get_combined_values()
warrior_ac = warrior.ac_bonus()

In [ ]:
acrobatics_skill_request = warrior.create_skill_check_request(warrior2.uuid, "acrobatics",warrior_ac.uuid)
perception_skill_request = warrior.create_skill_check_request(warrior2.uuid, "perception",warrior_ac.uuid)
strength_saving_throw_request = warrior.create_saving_throw_request(warrior2.uuid, "strength",warrior_ac.uuid)

In [ ]:
acrobatics_skill_request

In [ ]:
strength_saving_throw_request

In [ ]:
warrior2.skill_bonus(warrior.uuid,skill_name="acrobatics")

In [ ]:
warrior2.skill_check(acrobatics_skill_request)

In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
warrior2.saving_throw_bonus(warrior.uuid, "strength")

In [ ]:
warrior2.saving_throw(strength_saving_throw_request)


In [ ]:
from dnd.conditions import Blinded
from dnd.core.events import EventQueue


blinded = Blinded(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)
blinded.apply()



In [ ]:

warrior2.equipment.attack_bonus.advantage


In [ ]:
warrior.equipment.attack_bonus.advantage


In [ ]:
blinded.modifers_uuids

In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
blinded.remove()


In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
warrior2.equipment.attack_bonus.advantage


In [48]:
from dnd.core.modifiers import ContextualNumericalModifier, NumericalModifier, ContextAwareNumerical
from typing import Optional, Dict, Any
from uuid import UUID


In [49]:
from dnd.conditions import Charmed

charmed = Charmed(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)


In [ ]:
charmed.apply()


In [ ]:
deception_skill_request = warrior2.create_skill_check_request(warrior.uuid, "deception",15)

warrior.skill_check(deception_skill_request)





In [53]:
def hate_mona(source_entity_uuid: UUID, target_entity_uuid: Optional[UUID]=None, context: Optional[Dict[str, Any]]=None) -> NumericalModifier:
    """ function that cheks if the target name is Mona, in that case it gives a +5 modifier"""
    if target_entity_uuid is not None:
        target_entity = Entity.get(target_entity_uuid)
    else:
        target_entity = None
    if isinstance(target_entity, Entity) and target_entity.name == "Mona":
        return NumericalModifier(source_entity_uuid=source_entity_uuid, target_entity_uuid=target_entity_uuid, value=5)
    else:
        return NumericalModifier(source_entity_uuid=source_entity_uuid, target_entity_uuid=target_entity_uuid, value=0)

hate_mona_modifier = ContextualNumericalModifier(name="Hate Mona",source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid, callable=hate_mona)


In [ ]:
warrior.equipment.attack_bonus.self_contextual.add_value_modifier(hate_mona_modifier)


In [ ]:
warrior.set_target_entity(warrior2.uuid)
warrior.equipment.attack_bonus.normalized_score


In [ ]:
warrior.clear_target_entity()
warrior.equipment.attack_bonus.normalized_score


In [57]:
warrior.senses.entities[warrior2.uuid]=(1,0)

In [ ]:
from dnd.conditions import Frightened
frightened = Frightened(source_entity_uuid=warrior2.uuid, target_entity_uuid=warrior.uuid)
frightened.apply()






In [ ]:
warrior.action_economy.movement.normalized_score


In [ ]:
warrior.senses.entities = {}
warrior.action_economy.movement.normalized_score


In [ ]:
print(f"total_time: {time.time()-start_time}")